In [ ]:
from google.colab import drive
drive.mount('/content/drive')


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:


#import os
#os._exit(0)
#try:
#  # %tensorflow_version only exists in Colab.
#  %tensorflow_version 2.x
#except Exception:
#  pass

In [ ]:
!pip install ray==1.0.0
!pip install ax-platform #==0.1.17 Shoud be!
!pip install sqlalchemy==1.3.19 
!pip install nevergrad==0.4.2
!pip install configspace==0.4.15
!pip install zoopt==0.4.0
!pip install adabelief-pytorch==0.1.0
!pip install tensorboardX==2.1
!pip install HpBandSter==0.7.4

In [ ]:
# IN THIS MODULE: IMPORTS, CNN, TRAIN, TEST, MNIS_FUNCTION, SPACE

from __future__ import absolute_import
from __future__ import division
from __future__ import print_function
import numpy as np
import torch
import torch.optim as optim
import torch.nn as nn
from torchvision import datasets, transforms
from torch.utils.data import DataLoader
import torch.nn.functional as F
from ray import tune
from ray.tune.schedulers import ASHAScheduler
from hyperopt import hp
from ray.tune.suggest.hyperopt import HyperOptSearch
from ray.tune.suggest.skopt import SkOptSearch
from ray import tune
from ray.tune.suggest.bayesopt import BayesOptSearch
import time
import ray
from ray.tune.schedulers import AsyncHyperBandScheduler
from ray.tune.suggest.ax import AxSearch
import argparse
from ray.tune.suggest import ConcurrencyLimiter
from ray.tune.schedulers import AsyncHyperBandScheduler
from ray.tune.suggest.nevergrad import NevergradSearch
import nevergrad as ng
import json
import os
from ray.tune import Trainable
from ray.tune.schedulers.hb_bohb import HyperBandForBOHB
from ray.tune.suggest.bohb import TuneBOHB
from ray.tune.suggest import ConcurrencyLimiter
from ray.tune.schedulers import AsyncHyperBandScheduler
#from ray.tune.suggest.dragonfly import DragonflySearch
from ray.tune.suggest.zoopt import ZOOptSearch
from ray.tune.schedulers import AsyncHyperBandScheduler
from zoopt import ValueType
import torch
import adabelief_pytorch
global_checkpoint_period=np.inf

In [ ]:
from ray.tune import Stopper

class CustomStopper(Stopper):
    def __init__(self):
        self.should_stop = False

    def __call__(self, trial_id, result):
        if not self.should_stop and result['loss'] > 0.48:
          return True
        else:
          return False

    def stop_all(self):
        """Returns whether to stop trials and prevent new ones from starting."""
        return False



In [ ]:
def f_HyperOpt(dataset):
    
    scheduler = AsyncHyperBandScheduler(**experiment_metrics)
    bayesopt = HyperOptSearch(**experiment_metrics,max_concurrent=2)
    stopper = CustomStopper()
    tune.run(dataset, **tune_kwargs , scheduler = scheduler,  name="hyper", search_alg=bayesopt,resources_per_trial={'gpu': 1}, stop = stopper)

In [ ]:
def f_BayesOpt(dataset):
    
    scheduler = AsyncHyperBandScheduler(**experiment_metrics)
    bayesopt = BayesOptSearch(**experiment_metrics,max_concurrent=2)
      stopper = CustomStopper()

    tune.run(dataset, **tune_kwargs , scheduler = scheduler, name="bayes",  search_alg=bayesopt,resources_per_trial={'gpu': 1},stop = stopper)

In [ ]:
def f_AX(dataset):
    
   
    if __name__ == "__main__":
                
        algo = AxSearch(
            max_concurrent=2, #was working with 2
            **experiment_metrics
        )
        scheduler = AsyncHyperBandScheduler(**experiment_metrics)
        stopper = CustomStopper()
        tune.run(
            dataset,       name="ax",
            search_alg=algo,
            scheduler=scheduler,
            **tune_kwargs,resources_per_trial={'gpu': 1},stop = stopper)

        
#        algo = AxSearch(
#            **experiment_metrics
#        )
#        algo = ConcurrencyLimiter(algo, max_concurrent=4)

        
#        scheduler = AsyncHyperBandScheduler()
#        tune.run(
#            dataset,
#            **experiment_metrics,
#            search_alg=algo,
#            scheduler=scheduler,
#            **tune_kwargs)


In [ ]:

# TODO We are interested in multiple Population based algorithms from nevergrad, and certainly not in OnePlusOne. 
def f_NeverGrad(dataset):
    algo = NevergradSearch(
    optimizer=ng.optimizers.CMA
    # space=space,  # If you want to set the space manually
    )
    algo = ConcurrencyLimiter(algo, max_concurrent=2)

    scheduler = AsyncHyperBandScheduler()
    stopper = CustomStopper()
    tune.run(
        dataset,
        **experiment_metrics,
      #  name="nevergrad",
        search_alg=algo, name="ng",
        scheduler=scheduler,
        **tune_kwargs,resources_per_trial={'gpu': 1},stop = stopper)
    

In [ ]:
def f_BOHB(dataset):

    bohb_hyperband = HyperBandForBOHB(
        time_attr="training_iteration",
        max_t=100,
        reduction_factor=2,
        **experiment_metrics)

    bohb_search = TuneBOHB(
        # space=config_space, 
        max_concurrent=2,
        **experiment_metrics)
    stopper = CustomStopper()
    tune.run(
        dataset,
       # config=config, 
        scheduler=bohb_hyperband,name="bohb",
        search_alg=bohb_search,       
         **tune_kwargs,resources_per_trial={'gpu': 1},stop = stopper)
        #num_samples=NUM_TUNED,
       # stop={"training_iteration": 100})
    
    
    

In [ ]:
def f_Random(dataset):
    
    algo = NevergradSearch(
    optimizer=ng.optimizers.RandomSearch,
    # space=space,  # If you want to set the space manually,
    max_concurrent=2
    )
  #  algo = ConcurrencyLimiter(algo)

    scheduler = AsyncHyperBandScheduler()
    stopper = CustomStopper()
    tune.run(
        dataset,
        **experiment_metrics,
      #  name="nevergrad",
        search_alg=algo,   name="random",    
        scheduler=scheduler,
        **tune_kwargs,resources_per_trial={'gpu': 1},stop = stopper)
    

In [ ]:
def f_ZOOpt(dataset):

    dim_dict = {
        "lr": (ValueType.CONTINUOUS, [0, 1], 1e-2),
        "momentum": (ValueType.CONTINUOUS, [0,1, 0.9], 1e-2)
    }

    zoopt_search_config = {
        "parallel_num": 8,  # how many workers to parallel
    }

    
    stopper = CustomStopper()

    zoopt_search = ZOOptSearch(
    algo="Asracos",  # only support Asracos currently
    #dim_dict=dim_dict,
    budget=ITERATIONS,max_concurrent=2,
    #dim_dict=dim_dict,
   #     **zoopt_search_config,
    **experiment_metrics)
    
    scheduler = AsyncHyperBandScheduler(**experiment_metrics)

   
    tune.run(dataset,
 #        config = config,
    search_alg=zoopt_search,
   # num_samples= ITERATIONS,
    scheduler=scheduler,       
    #         paralell_num=4,
    name="zoopt_search", 
              **tune_kwargs,resources_per_trial={'gpu': 1},stop = stopper)
    

In [ ]:
class SentimentRNN(nn.Module):
    def __init__(self, embedding_dim, hidden_dim, output_size, n_layers,
             drop_prob, sigmoid , vocab_size,droupout_prob2):
        super(SentimentRNN, self).__init__()
        self.output_size = output_size
        self.n_layers = n_layers
        self.hidden_dim = hidden_dim

        self.embedding = nn.Embedding(vocab_size, embedding_dim)
        self.lstm = nn.LSTM(embedding_dim, hidden_dim, n_layers,
                            dropout=drop_prob, batch_first=True)
        #self.lstm = nn.GRU(embedding_dim, hidden_dim, n_layers, batch_first=True, dropout=drop_prob)

        self.dropout = nn.Dropout(droupout_prob2)

        self.fc = nn.Linear(hidden_dim, output_size)
        self.sig = nn.Sigmoid()

    def forward(self, x, hidden):
        hidden= tuple([each.data for each in hidden])
        batch_size = x.size(0)
        embeds = self.embedding(x)
        lstm_out, hidden = self.lstm(embeds, hidden)

        # stack up lstm outputs
        lstm_out = lstm_out.contiguous().view(-1, self.hidden_dim)

        # dropout and fully connected layer
        out = self.dropout(lstm_out)
        out = self.fc(out)

        # sigmoid function
        sig_out = self.sig(out)

        # reshape to be batch_size first
        sig_out = sig_out.view(batch_size, -1)
        sig_out = sig_out[:, -1] # get last batch of labels

        # return last sigmoid output and hidden state
        return sig_out, hidden


    def init_hidden(self, batch_size):
        weight = next(self.parameters()).data
        hidden = (weight.new(self.n_layers, batch_size, self.hidden_dim).zero_(),
                        weight.new(self.n_layers, batch_size, self.hidden_dim).zero_())
        return hidden


class SentimentRNN1(nn.Module):
    def __init__(self, embedding_dim, hidden_dim, output_size, n_layers,
             drop_prob, sigmoid , vocab_size,droupout_prob2):
        super(SentimentRNN1, self).__init__()
        self.output_size = output_size
        self.n_layers = n_layers
        self.hidden_dim = hidden_dim

        self.embedding = nn.Embedding(vocab_size, embedding_dim)
        #self.lstm = nn.LSTM(embedding_dim, hidden_dim, n_layers,
                        #    dropout=drop_prob, batch_first=True)
        self.lstm = nn.GRU(embedding_dim, hidden_dim, n_layers, batch_first=True, dropout=drop_prob)

        self.dropout = nn.Dropout(droupout_prob2)

        self.fc = nn.Linear(hidden_dim, output_size)
        self.sig = nn.Sigmoid()

    def forward(self, x, hidden):
        hidden = hidden.data
        batch_size = x.size(0)
        embeds = self.embedding(x)
        lstm_out, hidden = self.lstm(embeds, hidden)

        # stack up lstm outputs
        lstm_out = lstm_out.contiguous().view(-1, self.hidden_dim)

        # dropout and fully connected layer
        out = self.dropout(lstm_out)
        out = self.fc(out)

        # sigmoid function
        sig_out = self.sig(out)

        # reshape to be batch_size first
        sig_out = sig_out.view(batch_size, -1)
        sig_out = sig_out[:, -1] # get last batch of labels

        # return last sigmoid output and hidden state
        return sig_out, hidden


    def init_hidden(self, batch_size):
        weight = next(self.parameters()).data
        hidden = (weight.new(self.n_layers, batch_size, self.hidden_dim).zero_(),
                        weight.new(self.n_layers, batch_size, self.hidden_dim).zero_())
        (a,b) = hidden
        return a
    
class CNN(nn.Module):
    def __init__(self, vocab_size, embedding_dim, n_filters, filter_sizes, output_dim, 
                 dropout, pad_idx,sigmoid):

        super().__init__()

        self.embedding = nn.Embedding(vocab_size, embedding_dim)

        self.convs = nn.ModuleList([
                                    nn.Conv2d(in_channels = 1, 
                                              out_channels = n_filters, 
                                              kernel_size = (fs, embedding_dim)) 
                                    for fs in filter_sizes
                                    ])

        self.fc = nn.Linear(len(filter_sizes) * n_filters, output_dim)

        self.dropout = nn.Dropout(dropout)
        
        self.sigmoid = sigmoid
        self.sig = nn.Sigmoid()


    def forward(self, text):

        #text = [sent len, batch size]

       # text = text.permute(1, 0)
        #We want already have batch size, len for sentiment!!!!!
        #text = [batch size, sent len]

        embedded = self.embedding(text)

        #embedded = [batch size, sent len, emb dim]

        embedded = embedded.unsqueeze(1)

        #embedded = [batch size, 1, sent len, emb dim]

        conved = [self.sigmoid(conv(embedded)).squeeze(3) for conv in self.convs]

        #conv_n = [batch size, n_filters, sent len - filter_sizes[n]]

        pooled = [F.max_pool1d(conv, conv.shape[2]).squeeze(2) for conv in conved]

        #pooled_n = [batch size, n_filters]

        cat = self.dropout(torch.cat(pooled, dim = 1))

        #cat = [batch size, n_filters * len(filter_sizes)]
        sig_out = self.sig(self.fc(cat))

        # reshape to be batch_size first
        sig_out = sig_out.view(50, -1)
        #sig_out = sig_out[:, -1] # get last batch of labels

        # return last sigmoid output and hidden state
        return np.squeeze(sig_out)

In [ ]:
   #https://colab.research.google.com/github/agungsantoso/deep-learning-v2-pytorch/blob/master/sentiment-rnn/Sentiment_RNN_Exercise.ipynb#scrollTo=AVzirwGqpmva
def train_IMDB1(config):
    train_x = np.load('/content/drive/My Drive/train_x.npy')
    train_y = np.load('/content/drive/My Drive/train_y.npy')
    val_x = np.load('/content/drive/My Drive/val_x.npy')
    val_y = np.load('/content/drive/My Drive/val_y.npy')
    test_x = np.load('/content/drive/My Drive/test_x.npy')
    test_y = np.load('/content/drive/My Drive/test_y.npy')
    len_vocab_to_int = 74072
    ## print out the shapes of your resultant feature data
    from torch.utils.data import TensorDataset, DataLoader
    #print(train_x.shape)
    import torch

    # create Tensor datasets
    train_data = TensorDataset(torch.from_numpy(train_x), torch.from_numpy(train_y))
    valid_data = TensorDataset(torch.from_numpy(val_x), torch.from_numpy(val_y))
    test_data = TensorDataset(torch.from_numpy(test_x), torch.from_numpy(test_y))

    # dataloaders
    batch_size = 50

    # make sure to SHUFFLE your data
    train_loader = DataLoader(train_data, shuffle=True, batch_size=batch_size)
    valid_loader = DataLoader(valid_data, shuffle=True, batch_size=batch_size)
    test_loader = DataLoader(test_data, shuffle=True, batch_size=batch_size)
    # obtain one batch of training data
    dataiter = iter(train_loader)
    sample_x, sample_y = dataiter.next()

    # First checking if GPU is available
    train_on_gpu=torch.cuda.is_available()


    sigmoid_func_uniq = get_sigmoid_func(config.get("sigmoid_func", 0))       
        
        
    # Instantiate the model w/ hyperparams
    vocab_size = len_vocab_to_int + 1 # +1 for zero padding + our word tokens
    output_size = 1
    embedding_dim = int(round(config.get("embedding",64)))
    hidden_dim = int(round(config.get("hidden_dim",64)))
    n_layers =  1+ int( round(config.get("n_layer",1)))
    dropout_2 = config.get("droupout_prob2",0.3);

    FILTER_SIZES = [2,3,4]
    PAD_IDX = 4    


    if(config.get("model",0)<1/3):
        net = SentimentRNN(embedding_dim, hidden_dim, output_size, n_layers,
                           config.get("droupout_prob",0.1),
                           sigmoid_func_uniq, vocab_size,dropout_2)    
    elif(config.get("model",0)<2/3):
        net = SentimentRNN1(embedding_dim, hidden_dim, output_size, n_layers,
                           config.get("droupout_prob",0.1),
                           sigmoid_func_uniq, vocab_size,dropout_2)
    else:
        net = CNN(vocab_size, embedding_dim, hidden_dim, FILTER_SIZES, 
              output_size, config.get("droupout_prob",0.1), PAD_IDX,sigmoid_func_uniq)
    # loss and optimization functions 


        # loss and optimization functions
    lr=10**(-config.get("lr", 1))
    wd=10**(-config.get("weight_decay", 1))

    criterion = nn.L1Loss()
    
    
    if(config.get("adam",0)>0.5):
        optimizer = torch.optim.Adam(net.parameters(), lr=lr, 
           weight_decay=wd, 
                                         amsgrad=True)
    else: 
        optimizer = adabelief_pytorch.AdaBelief(net.parameters(), lr=lr, 
                              weight_decay=wd)
    


        # training params

    epochs = ITERATIONS # 3-4 is approx where I noticed the validation loss stop decreasing

    counter = 0
    print_every = 10
    clip=1 # gradient clipping



    # move model to GPU, if available
    if(train_on_gpu):
        net.cuda()

    net.train()
    # train for some number of epochs
    
    
    def trainlstm():
     #   criterion = nn.BCELoss()

         # initialize hidden state
        h = net.init_hidden(batch_size)

        # batch loop
        for inputs, labels in train_loader:

            if(train_on_gpu):
                inputs, labels = inputs.cuda(), labels.cuda()

            # Creating new variables for the hidden state, otherwise
            # we'd backprop through the entire training history
            
            
            
            h = tuple([each.data for each in h])
            # zero accumulated gradients
            net.zero_grad()

            # get the output from the model
            output, h = net(inputs, h)

            # calculate the loss and perform backprop
            loss = criterion(output.squeeze(), labels.float())
            loss.backward()
            # `clip_grad_norm` helps prevent the exploding gradient problem in RNNs / LSTMs.
            nn.utils.clip_grad_norm_(net.parameters(), clip)
            optimizer.step()

    def traingru():
        h = net.init_hidden(batch_size)
     #   criterion = nn.BCELoss()

        # batch loop
        for inputs, labels in train_loader:

            if(train_on_gpu):
                inputs, labels = inputs.cuda(), labels.cuda()

            # Creating new variables for the hidden state, otherwise
            # we'd backprop through the entire training history
            
            
            
           # h = tuple([each.data for each in h])
            h = h.data
            # zero accumulated gradients
            net.zero_grad()

            # get the output from the model
            output, h = net(inputs, h)

            # calculate the loss and perform backprop
            loss = criterion(output.squeeze(), labels.float())
            loss.backward()
            # `clip_grad_norm` helps prevent the exploding gradient problem in RNNs / LSTMs.
            nn.utils.clip_grad_norm_(net.parameters(), clip)
            optimizer.step()
       
    
    def train_cnn():
       # criterion = nn.BCELoss()

        device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
        net.train()
        #for (data, target) in train_loader:
        for batch_idx, (inputs, labels) in enumerate(train_loader):
            # We set this just for the example to run quickly.
            if(train_on_gpu):
                inputs, labels = inputs.cuda(), labels.cuda()


            optimizer.zero_grad()
            output = net(inputs)

            loss = criterion(output.squeeze(), labels.float())
            loss.backward()
            optimizer.step()
    
    def test_lstm(x):
       
        val_h = net.init_hidden(batch_size)
        val_losses = []
        net.eval()
        for inputs, labels in x:

            # Creating new variables for the hidden state, otherwise
            # we'd backprop through the entire training history

            val_h = tuple([each.data for each in val_h])
            if(train_on_gpu):
                inputs, labels = inputs.cuda(), labels.cuda()

            output, val_h = net(inputs, val_h)
            val_loss = criterion(output.squeeze(), labels.float())

            val_losses.append(val_loss.item())

        net.train()
        return np.mean(val_losses) 

            
    def test_gru(x):
        
        val_h = net.init_hidden(batch_size)
        val_losses = []
        net.eval()
        for inputs, labels in x:

            # Creating new variables for the hidden state, otherwise
            # we'd backprop through the entire training history

            #val_h = tuple([each.data for each in val_h])
            val_h = val_h.data
            if(train_on_gpu):
                inputs, labels = inputs.cuda(), labels.cuda()

            output, val_h = net(inputs, val_h)
            val_loss = criterion(output.squeeze(), labels.float())

            val_losses.append(val_loss.item())

        net.train()
    
        return np.mean(val_losses) 
    
    def test_cnn(x):
        val_losses = []
        net.eval()
        for inputs, labels in x:
            if(train_on_gpu):
                inputs, labels = inputs.cuda(), labels.cuda()
            output = net(inputs)
            val_loss = criterion(output.squeeze(), labels.float())

            val_losses.append(val_loss.item())

         
        net.train()
    
        return np.mean(val_losses)     
            

    for e in range(epochs):

       
        model = config.get("model",0)
        if(model<1/3) :
            trainlstm()
            loss=test_lstm(valid_loader)
            acc = test_lstm(test_loader)

        elif(model<2/3):
            traingru()
            loss=test_gru(valid_loader)
            acc = test_gru(test_loader)
        else:
            train_cnn()
            loss=test_cnn(valid_loader)
            acc = test_cnn(test_loader)
               
        tune.report(loss=loss,mean_accuracy=acc)



In [ ]:
#Configs
parser = argparse.ArgumentParser()
parser.add_argument(
    "--smoke_test", action="store_false", help="Finish not quickly for testing")
args, _ = parser.parse_known_args()          
        
    
    
#experiment_metrics = dict(metric="mean_accuracy", mode="max")
experiment_metrics = dict(metric="loss", mode="min")


ITERATIONS = 4
NUM_TUNED=  128
    

#i is in [0;1]
#We want all values between 0 and 1
def get_sigmoid_func(i):
    if(i<0.33):
        return nn.ReLU()
    elif(i<0.67):
        return nn.Tanh()
    else:
        return nn.Sigmoid()





tune_kwargs = {
    "num_samples": NUM_TUNED if args.smoke_test else NUM_TUNED,
    "config": {
    "steps": ITERATIONS,  
     "lr": tune.uniform(2, 7 ) #will be x->10**-x
       ,  "embedding": tune.uniform(200, 1024) #Pas bien #Different embeddings, fine tune ou pas
      ,"droupout_prob2":tune.uniform(0.3,0.6)
         ,"weight_decay": tune.uniform(2,7) #will be x->10**-x
      ,  "sigmoid_func":tune.uniform(0,1),
        "hidden_dim":tune.uniform(32.,512.),
        "n_layer":tune.uniform(1,5),
        "droupout_prob":tune.uniform(0.3,0.6)  
     ,   "adam":tune.uniform(0,1)
      ,  "model":tune.uniform(0,1)
    }
}


#x_all = [train_IMDB,  train_TREC, train_boston, train_diabetes, train_mnist, train_fashion_mnist]

#f_HyperOpt(train_IMDB1)

#f_HyperOpt(train_IMDB1) 

In [ ]:
for i in range(0,1):
    for j in range(0,1):
        x = train_IMDB1
        f_BayesOpt(x)
        #f_AX(x)
        #f_NeverGrad(x)
        #f_BOHB(x)
        #f_Random(x)
        #f_ZOOpt(x)
        print("all worked with " + str(x)+  " !")

INFO:ray.tune.ray_trial_executor:Initializing Ray automatically.For cluster usage or custom Ray initialization, call `ray.init(...)` before `tune.run`.
2020-11-25 23:34:31,837	INFO services.py:1166 -- View the Ray dashboard at http://127.0.0.1:8265
2020-11-25 23:34:34,043	WARNING function_runner.py:486 -- Function checkpointing is disabled. This may result in unexpected behavior when using checkpointing features or certain schedulers. To enable, set the train function arguments to be `func(config, checkpoint_dir=None)`.


(pid=650) Please check your arguments if you have upgraded adabelief-pytorch from version 0.0.5.
(pid=650) Modifications to default arguments:
(pid=650)                            eps  weight_decouple    rectify
(pid=650) -----------------------  -----  -----------------  ---------
(pid=650) adabelief-pytorch=0.0.5  1e-08  False              False
(pid=650) Current version (0.1.0)  1e-16  True               True
(pid=650) For a complete table of recommended hyperparameters, see
(pid=650) https://github.com/juntang-zhuang/Adabelief-Optimizer
(pid=650) 
(pid=650) Weight decoupling enabled in AdaBelief
(pid=650) Rectification enabled in AdaBelief
Result for train_IMDB1_c61ba658:
  date: 2020-11-25_23-35-16
  done: true
  experiment_id: d8db94acf84c4ef8bacaa700162077a2
  experiment_tag: 1_adam=0.45609,droupout_prob=0.37471,droupout_prob2=0.40455,embedding=473.66,hidden_dim=149.83,lr=6.569,model=0.28478,n_layer=2.1635,sigmoid_func=0.12043,steps=4,weight_decay=5.9717
  hostname: 15d076f80459

(pid=649) Please check your arguments if you have upgraded adabelief-pytorch from version 0.0.5.
(pid=649) Modifications to default arguments:
(pid=649)                            eps  weight_decouple    rectify
(pid=649) -----------------------  -----  -----------------  ---------
(pid=649) adabelief-pytorch=0.0.5  1e-08  False              False
(pid=649) Current version (0.1.0)  1e-16  True               True
(pid=649) For a complete table of recommended hyperparameters, see
(pid=649) https://github.com/juntang-zhuang/Adabelief-Optimizer
(pid=649) 
(pid=649) Weight decoupling enabled in AdaBelief
(pid=649) Rectification enabled in AdaBelief
Result for train_IMDB1_c61facb2:
  date: 2020-11-25_23-36-08
  done: true
  experiment_id: a45b995508fe4932b63eec97975b871b
  experiment_tag: 2_adam=0.48105,droupout_prob=0.5429,droupout_prob2=0.55555,embedding=931.31,hidden_dim=138.87,lr=3.3273,model=0.20957,n_layer=3.2685,sigmoid_func=0.42467,steps=4,weight_decay=5.5475
  hostname: 15d076f80459

(pid=761) Please check your arguments if you have upgraded adabelief-pytorch from version 0.0.5.
(pid=761) Modifications to default arguments:
(pid=761)                            eps  weight_decouple    rectify
(pid=761) -----------------------  -----  -----------------  ---------
(pid=761) adabelief-pytorch=0.0.5  1e-08  False              False
(pid=761) Current version (0.1.0)  1e-16  True               True
(pid=761) For a complete table of recommended hyperparameters, see
(pid=761) https://github.com/juntang-zhuang/Adabelief-Optimizer
(pid=761) 
(pid=761) Weight decoupling enabled in AdaBelief
(pid=761) Rectification enabled in AdaBelief
Result for train_IMDB1_df4b4d04:
  date: 2020-11-25_23-36-32
  done: true
  experiment_id: 3cfcdd62ea914103ac9947d7fcc10a2c
  experiment_tag: 3_adam=0.42993,droupout_prob=0.38375,droupout_prob2=0.39894,embedding=298.41,hidden_dim=407.85,lr=5.4627,model=0.9489,n_layer=4.5639,sigmoid_func=0.58251,steps=4,weight_decay=4.6399
  hostname: 15d076f80459

2020-11-25 23:36:33,252	WARNING worker.py:1072 -- The actor or task with ID ffffffffffffffffa628090a01000000 is pending and cannot currently be scheduled. It requires {GPU: 1.000000}, {CPU: 1.000000} for execution and {GPU: 1.000000}, {CPU: 1.000000} for placement, but this node only has remaining {GPU: 1.000000}, {node:172.28.0.2: 1.000000}, {accelerator_type:T4: 1.000000}, {CPU: 2.000000}, {memory: 7.177734 GiB}, {object_store_memory: 2.441406 GiB}. In total there are 0 pending tasks and 1 pending actors on this node. This is likely due to all cluster resources being claimed by actors. To resolve the issue, consider creating fewer actors or increase the resources available to this Ray cluster. You can ignore this message if this Ray cluster is expected to auto-scale.
2020-11-25 23:36:33,676	INFO (unknown file):0 -- gc.collect() freed 112 refs in 0.32700951300000725 seconds


...

(pid=4276) Please check your arguments if you have upgraded adabelief-pytorch from version 0.0.5.
(pid=4276) Modifications to default arguments:
(pid=4276)                            eps  weight_decouple    rectify
(pid=4276) -----------------------  -----  -----------------  ---------
(pid=4276) adabelief-pytorch=0.0.5  1e-08  False              False
(pid=4276) Current version (0.1.0)  1e-16  True               True
(pid=4276) For a complete table of recommended hyperparameters, see
(pid=4276) https://github.com/juntang-zhuang/Adabelief-Optimizer
(pid=4276) 
(pid=4276) Weight decoupling enabled in AdaBelief
(pid=4276) Rectification enabled in AdaBelief
Result for train_IMDB1_343986a4:
  date: 2020-11-26_02-09-51
  done: true
  experiment_id: b1ca90997fde43f790d9d25367a0374c
  experiment_tag: 126_adam=0.44962,droupout_prob=0.49411,droupout_prob2=0.52048,embedding=661.72,hidden_dim=445.13,lr=4.9055,model=0.93919,n_layer=2.8414,sigmoid_func=0.309,steps=4,weight_decay=2.3734
  hostname: 

Result for train_IMDB1_5dc564ac:
  date: 2020-11-26_02-10-27
  done: true
  experiment_id: d0589b0821f2427b968e8f4d48b0fe92
  experiment_tag: 127_adam=0.88529,droupout_prob=0.43176,droupout_prob2=0.37767,embedding=322.33,hidden_dim=243.17,lr=2.4976,model=0.55117,n_layer=1.5447,sigmoid_func=0.58932,steps=4,weight_decay=4.2068
  hostname: 15d076f80459
  iterations_since_restore: 1
  loss: 0.5000000828504563
  mean_accuracy: 0.49999996602535246
  node_ip: 172.28.0.2
  pid: 4303
  time_since_restore: 34.55939292907715
  time_this_iter_s: 34.55939292907715
  time_total_s: 34.55939292907715
  timestamp: 1606356627
  timesteps_since_restore: 0
  training_iteration: 1
  trial_id: 5dc564ac
  


(pid=4330) Please check your arguments if you have upgraded adabelief-pytorch from version 0.0.5.
(pid=4330) Modifications to default arguments:
(pid=4330)                            eps  weight_decouple    rectify
(pid=4330) -----------------------  -----  -----------------  ---------
(pid=4330) adabelief-pytorch=0.0.5  1e-08  False              False
(pid=4330) Current version (0.1.0)  1e-16  True               True
(pid=4330) For a complete table of recommended hyperparameters, see
(pid=4330) https://github.com/juntang-zhuang/Adabelief-Optimizer
(pid=4330) 
(pid=4330) Weight decoupling enabled in AdaBelief
(pid=4330) Rectification enabled in AdaBelief
Result for train_IMDB1_77dad6ba:
  date: 2020-11-26_02-11-47
  done: true
  experiment_id: ea3a1460359443f4872c0f17c545663a
  experiment_tag: 128_adam=0.15201,droupout_prob=0.44957,droupout_prob2=0.34094,embedding=826.08,hidden_dim=299.59,lr=3.4562,model=0.62783,n_layer=3.6233,sigmoid_func=0.43734,steps=4,weight_decay=2.9659
  hostname

2020-11-26 02:11:48,612	WARNING suggestion.py:69 -- DeprecationWarning: `max_concurrent` is deprecated for this search algorithm. Use tune.suggest.ConcurrencyLimiter() instead. This will raise an error in future versions of Ray.


NameError: ignored